In [ ]:
# Install required packages
!pip install transformers datasets torch pandas scikit-learn
!pip install transformers[torch] accelerate -U

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 547.8/547.8 kB 6.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 40.8/40.8 MB 7.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 8.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 64.9/64.9 kB 3.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 4.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 9.7 MB/s eta 0:00:00
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (23.7 MB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (823 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (14.1 MB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl (731.7 MB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl (410.6 MB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl (121

In [ ]:
from datasets import load_dataset
from transformers import BertTokenizer, BertForSequenceClassification, Trainer, TrainingArguments
from sklearn.metrics import accuracy_score, precision_recall_fscore_support
import torch
import numpy as np

In [ ]:
# Load the dataset
dataset = load_dataset('CodeHima/TOS_Dataset')

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Generating train split:   0%|          | 0/5378 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/415 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/1038 [00:00<?, ? examples/s]

In [ ]:
# Initialize the tokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

tokenizer_config.json:   0%|          | 0.00/48.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/570 [00:00<?, ?B/s]

In [ ]:
# Create label mapping
label_mapping = {'clearly_fair': 0, 'potentially_unfair': 1, 'clearly_unfair': 2}

In [ ]:
def tokenize_and_encode(examples):
    tokenized = tokenizer(examples['sentence'], padding='max_length', truncation=True, max_length=512)
    tokenized['labels'] = [label_mapping[label] for label in examples['unfairness_level']]
    return tokenized

In [ ]:
# Tokenize and encode the dataset
tokenized_dataset = dataset.map(tokenize_and_encode, batched=True)

# Set the format for PyTorch
tokenized_dataset.set_format(type='torch', columns=['input_ids', 'attention_mask', 'labels'])

Map:   0%|          | 0/5378 [00:00<?, ? examples/s]

Map:   0%|          | 0/415 [00:00<?, ? examples/s]

Map:   0%|          | 0/1038 [00:00<?, ? examples/s]

In [ ]:
# Split the dataset
train_data = tokenized_dataset['train']
validation_data = tokenized_dataset['validation']
test_data = tokenized_dataset['test']

In [ ]:
# Load the model
num_labels = 3  # clearly_fair, potentially_unfair, clearly_unfair
model = BertForSequenceClassification.from_pretrained('bert-base-uncased', num_labels=num_labels)

model.safetensors:   0%|          | 0.00/440M [00:00<?, ?B/s]

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [ ]:
# Define training arguments
training_args = TrainingArguments(
    output_dir='./results',
    num_train_epochs=3,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    warmup_steps=500,
    weight_decay=0.01,
    logging_dir='./logs',
    logging_steps=10,
    evaluation_strategy="epoch"
)

/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1494: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


In [ ]:
# Define the compute metrics function
def compute_metrics(pred):
    labels = pred.label_ids
    preds = np.argmax(pred.predictions, axis=-1)
    precision, recall, f1, _ = precision_recall_fscore_support(labels, preds, average='weighted')
    acc = accuracy_score(labels, preds)
    return {
        'accuracy': acc,
        'f1': f1,
        'precision': precision,
        'recall': recall
    }

In [ ]:
# Initialize the Trainer
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_data,
    eval_dataset=validation_data,
    compute_metrics=compute_metrics
)

In [ ]:
# Train the model
trainer.train()

TrainOutput(global_step=1011, training_loss=0.3412421460969983, metrics={'train_runtime': 1424.0162, 'train_samples_per_second': 11.33, 'train_steps_per_second': 0.71, 'total_flos': 4245071881623552.0, 'train_loss': 0.3412421460969983, 'epoch': 3.0})

In [ ]:
# Evaluate the model on validation data
validation_results = trainer.evaluate(eval_dataset=validation_data)
print(f"Validation Accuracy: {validation_results['eval_accuracy']}")

# Evaluate the model on test data
test_results = trainer.evaluate(eval_dataset=test_data)
print(f"Test Accuracy: {test_results['eval_accuracy']}")

Validation Accuracy: 0.8891566265060241
Test Accuracy: 0.8795761078998073


In [ ]:
# Save the model
model.save_pretrained('./tos-bert-classifier-v2')
tokenizer.save_pretrained('./tos-bert-classifier-v2')

('./tos-bert-classifier-v2/tokenizer_config.json',
 './tos-bert-classifier-v2/special_tokens_map.json',
 './tos-bert-classifier-v2/vocab.txt',
 './tos-bert-classifier-v2/added_tokens.json')

In [ ]:
# Function to predict unfairness level
def predict_unfairness(text, model, tokenizer):
    inputs = tokenizer(text, return_tensors="pt", truncation=True, padding=True, max_length=512)

    model.eval()
    with torch.no_grad():
        outputs = model(**inputs)

    probabilities = torch.softmax(outputs.logits, dim=-1).squeeze()
    predicted_class = torch.argmax(probabilities).item()

    inverse_label_mapping = {0: 'clearly_fair', 1: 'potentially_unfair', 2: 'clearly_unfair'}
    predicted_label = inverse_label_mapping[predicted_class]

    return predicted_label, probabilities.tolist()

In [ ]:
# Test the model
def test_model():
    model_path = './tos-bert-classifier-v2'
    model = BertForSequenceClassification.from_pretrained(model_path)
    tokenizer = BertTokenizer.from_pretrained(model_path)

    while True:
        text = input("Enter a clause to classify (or 'quit' to exit): ")
        if text.lower() == 'quit':
            break

        predicted_label, probabilities = predict_unfairness(text, model, tokenizer)

        print(f"\nPredicted unfairness level: {predicted_label}")
        print("Probabilities:")
        for label, prob in zip(['clearly_fair', 'potentially_unfair', 'clearly_unfair'], probabilities):
            print(f"{label}: {prob:.4f}")
        print()

if __name__ == "__main__":
    test_model()

Enter a clause to classify (or 'quit' to exit): 3. We reserve the right to suspend, terminate, or restrict your access to the platform at any time and for any reason, without prior notice or explanation. This includes but is not limited to violations of our community guidelines or terms of service, as determined solely by ConnectWorld.

Predicted unfairness level: potentially_unfair
Probabilities:
clearly_fair: 0.0293
potentially_unfair: 0.5666
clearly_unfair: 0.4042

Enter a clause to classify (or 'quit' to exit): You have the right to use CommunityConnect for its intended purpose of connecting with others, sharing content responsibly, and engaging in constructive dialogue. You are responsible for the content you post and must respect the rights and privacy of others.

Predicted unfairness level: clearly_fair
Probabilities:
clearly_fair: 0.9985
potentially_unfair: 0.0008
clearly_unfair: 0.0008

Enter a clause to classify (or 'quit' to exit): Our community guidelines are designed to ma

In [ ]:
# Upload to Hugging Face Hub
from huggingface_hub import HfApi, Repository
import os

In [ ]:
# Set your Hugging Face token and repo name
hf_token = "Your_HF_Token"
repo_name = "TOSBertV2"

# Initialize Hugging Face API
api = HfApi()

In [ ]:
# Create a new repository
repo_url = api.create_repo(
    repo_id=repo_name,
    token=hf_token,
    private=False,
    exist_ok=True
)

In [ ]:
# Clone the empty repository
repo = Repository(local_dir=repo_name, clone_from=repo_url, use_auth_token=hf_token)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_deprecation.py:131: FutureWarning: 'Repository' (from 'huggingface_hub.repository') is deprecated and will be removed from version '1.0'. Please prefer the http-based alternatives instead. Given its large adoption in legacy code, the complete removal is only planned on next major release.
For more details, please read https://huggingface.co/docs/huggingface_hub/concepts/git_vs_http.
  warnings.warn(warning_message, FutureWarning)
Cloning https://huggingface.co/CodeHima/TOSBertV2 into local empty directory.


In [ ]:
# Load your trained model and tokenizer
model = BertForSequenceClassification.from_pretrained('./tos-bert-classifier-v2')
tokenizer = BertTokenizer.from_pretrained('./tos-bert-classifier-v2')

In [ ]:
# Save the model and tokenizer to the cloned repository
model.save_pretrained(repo_name)
tokenizer.save_pretrained(repo_name)

('TOSBertV2/tokenizer_config.json',
 'TOSBertV2/special_tokens_map.json',
 'TOSBertV2/vocab.txt',
 'TOSBertV2/added_tokens.json')

In [ ]:
# Add a README file
with open(os.path.join(repo_name, "README.md"), "w") as f:
    f.write("# TOSBertV2\n\nThis model is trained to classify clauses in Terms of Service (ToS) documents into three unfairness levels: clearly_fair, potentially_unfair, and clearly_unfair.")

# Push the files to the Hugging Face Hub
repo.git_add()
repo.git_commit("Initial commit")
repo.git_push()

print(f"Model successfully pushed to https://huggingface.co/{repo_name}")

Upload file model.safetensors:   0%|          | 1.00/418M [00:00<?, ?B/s]

remote: -------------------------------------------------------------------------        
remote: Your push was accepted, but with warnings:         
remote: - Warning: empty or missing yaml metadata in repo card        
remote: help: https://huggingface.co/docs/hub/model-cards#model-card-metadata        
remote: -------------------------------------------------------------------------        
remote: -------------------------------------------------------------------------        
remote: Please find the documentation at:        
remote: https://huggingface.co/docs/hub/model-cards#model-card-metadata        
remote:         
remote: -------------------------------------------------------------------------        
To https://huggingface.co/CodeHima/TOSBertV2
   5e43a01..d02db41  main -> main

remote: Your push was accepted, but with warnings:         
remote: - Warning: empty or missing yaml metadata in repo card        
remote: help: https://huggingface.co/docs/hub/model-cards#model-c

Model successfully pushed to https://huggingface.co/TOSBertV2
